In [36]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import datetime
import glob
import seaborn as sns
import statsmodels.api as sm
import sklearn.preprocessing

In [37]:
# Read in rb stats files
qbStatsFiles = [filename for filename in glob.glob("C:/Users/Michael/Desktop/Springboard/Capstone2/csvFiles/DFS_Data/QB/stats/*.csv")]
qbStatsFiles[0]

'C:/Users/Michael/Desktop/Springboard/Capstone2/csvFiles/DFS_Data/QB/stats\\QB2011.csv'

In [38]:
# Extract season and fix playoff weeks to match other tables

dfs = []
dfsPlayoffs = []

for i in range(int(len(qbStatsFiles)/2)):
    df = pd.read_csv(qbStatsFiles[i])
    df['season'] = qbStatsFiles[i][-8:-4]
    dfs.append(df)

# second half of list has playoff games, need to fix their weeks, then combine with first table    
for i in range(int(len(qbStatsFiles)/2),int(len(qbStatsFiles)/2)*2):
    dfPlayoffs = pd.read_csv(qbStatsFiles[i])
    dfPlayoffs['season'] = qbStatsFiles[i][-8:-4]
    dfsPlayoffs.append(dfPlayoffs)

    
for i in range(len(dfsPlayoffs)):
    dfsPlayoffs[i].loc[dfsPlayoffs[i].Week == 1, 'Week'] = 18
    dfsPlayoffs[i].loc[dfsPlayoffs[i].Week == 2, 'Week'] = 19
    dfsPlayoffs[i].loc[dfsPlayoffs[i].Week == 3, 'Week'] = 20
    dfsPlayoffs[i].loc[dfsPlayoffs[i].Week == 4, 'Week'] = 21


# dfsPlayoffs[-1].head()

qb = pd.concat(dfs,axis=0)
qb = qb.append(dfsPlayoffs)
qb.head()

Rank              Name Team Position  Week Opponent  PassingCompletions  \
0     1     Aaron Rodgers   GB       QB     4      DEN                  29   
1     2  Matthew Stafford  DET       QB    17       GB                  36   
2     3        Matt Flynn   GB       QB    17      DET                  31   
3     4        Cam Newton  CAR       QB    13       TB                  12   
4     5        Drew Brees   NO       QB    12      NYG                  24   

   PassingAttempts  PassingCompletionPercentage  PassingYards  ...  \
0               38                         76.3           408  ...   
1               59                         61.0           520  ...   
2               44                         70.5           480  ...   
3               21                         57.1           204  ...   
4               38                         63.2           363  ...   

   PassingTouchdowns  PassingInterceptions  PassingRating  RushingAttempts  \
0                  4                     1         134.54                9   
1                  5                     2         103.78                0   
2                  6                     1         136.36                2   
3                  1                     0         106.05               14   
4                  4                     0         129.61                1   

   RushingYards  RushingYardsPerAttempt  RushingTouchdowns  \
0            36                     4.0                  2   
1             0                     0.0                  0   
2             0                     0.0                  0   
3            54                     3.9                  3   
4             8                     8.0                  1   

   FantasyPointsPerGameFanDuel  FantasyPointsFanDuel  season  
0                         46.9                 46.92    2011  
1                         40.8                 40.80    2011  
2                         40.2                 40.20    2011  
3                         38.8                 38.76    2011  
4                         37.3                 37.32    2011  

[5 rows x 21 columns]

In [39]:
# Pull data from other workbooks
awayMatchup = pd.read_csv('C://Users//Michael//Desktop//Springboard//Capstone2//csvFiles//awayMatchup.csv',index_col=0)
homeMatchup = pd.read_csv('C://Users//Michael//Desktop//Springboard//Capstone2//csvFiles//homeMatchup.csv',index_col=0)
oddsTable = pd.read_csv('C://Users//Michael//Desktop//Springboard//Capstone2//csvFiles//oddsTable.csv',index_col=0)
finalTeamGameDataTable = pd.read_csv('C://Users//Michael//Desktop//Springboard//Capstone2//csvFiles//teamGameData.csv',index_col=0)
rollAvgGameData = pd.read_csv('C://Users//Michael//Desktop//Springboard//Capstone2//csvFiles//rollAvgGameData.csv',index_col=0)
%store -r awayTable
%store -r homeTable

In [40]:
awayMatchup[awayMatchup['week'] == 1]

Empty DataFrame
Columns: [gameId, date, season, week, team_x, homeAway, stadium, roof, surface, avgPf, avgOvr_x, avgOff, avgPass, avgPblk, avgRecv, avgRun, avgRblk, totalDvoa_x, offDvoa, stDvoa, overUnder, pa, totalScore, team_y, avgPa, avgOvr_y, avgDef, avgRdef, avgPrsh, avgCov, totalDvoa_y, defDvoa, ptsMatchup, offMatchup, ovrMatchup, passMatchup, pblkMatchup, runMatchup, offDvoaMatchup, totalDvoaMatchup, pf]
Index: []

[0 rows x 41 columns]

In [41]:
awayMatchup

gameId        date  season  week               team_x homeAway  \
0     201811110kan  2018-11-11    2018    10    Arizona Cardinals     away   
1     201610300car  2016-10-30    2016     8    Arizona Cardinals     away   
2     201612240sea  2016-12-24    2016    16    Arizona Cardinals     away   
3     201812300sea  2018-12-30    2018    17    Arizona Cardinals     away   
4     201712310sea  2017-12-31    2017    17    Arizona Cardinals     away   
...            ...         ...     ...   ...                  ...      ...   
2934  200711180dal  2007-11-18    2007    11  Washington Redskins     away   
2935  200809280dal  2008-09-28    2008     4  Washington Redskins     away   
2936  201410120crd  2014-10-12    2014     6  Washington Redskins     away   
2937  201012250crd  2010-12-25    2010    16       Dallas Cowboys     away   
2938  201012130min  2010-12-13    2010    14      New York Giants     away   

                            stadium      roof surface      avgPf  ...  \
0                 Arrowhead Stadium  outdoors   grass  14.857143  ...   
1           Bank of America Stadium  outdoors   grass  22.714286  ...   
2                 CenturyLink Field  outdoors    turf  25.857143  ...   
3                 CenturyLink Field  outdoors    turf  13.000000  ...   
4                 CenturyLink Field  outdoors    turf  18.571429  ...   
...                             ...       ...     ...        ...  ...   
2934                  Texas Stadium  outdoors    turf  20.142857  ...   
2935                  Texas Stadium  outdoors    turf  22.142857  ...   
2936  University of Phoenix Stadium      dome   grass  20.142857  ...   
2937  University of Phoenix Stadium      dome   grass  28.571429  ...   
2938                     Ford Field      dome    turf  28.857143  ...   

      defDvoa  ptsMatchup  offMatchup  ovrMatchup  passMatchup  pblkMatchup  \
0       0.065   37.857143  -10.285714  -13.857143   -10.600000   -16.071429   
1       0.036   51.285714    3.000000    4.457143    -2.228571     3.257143   
2      -0.114   43.857143    0.757143   -3.042857     7.171429   -14.242857   
3       0.016   36.857143   -7.400000  -13.642857    -7.628571    -6.100000   
4      -0.036   41.000000   -9.228571   -2.514286   -15.628571    -5.085714   
...       ...         ...         ...         ...          ...          ...   
2934   -0.138   40.142857   -4.571429   -9.700000     1.785714    12.114286   
2935    0.033   41.285714   11.628571    5.371429    14.628571    10.242857   
2936   -0.144   42.000000    3.171429   -2.271429     4.500000    20.400000   
2937    0.074   53.142857   14.557143    9.057143     8.200000    11.028571   
2938    0.033   52.428571    9.371429    4.757143    21.157143     0.800000   

      runMatchup  offDvoaMatchup  totalDvoaMatchup  pf  
0       0.657143          -0.315            -0.700  14  
1      -3.157143          -0.039             0.208  20  
2      -9.314286          -0.250            -0.160  34  
3      -7.414286          -0.409            -0.500  24  
4      -6.285714          -0.227            -0.159  26  
...          ...             ...               ...  ..  
2934  -28.028571          -0.241            -0.434  23  
2935   -7.057143           0.187            -0.488  26  
2936  -16.614286          -0.111            -0.216  20  
2937   -2.385714           0.072             0.213  26  
2938   -8.614286           0.155             0.324  21  

[2939 rows x 41 columns]

In [42]:
# Clean up the Team column to match the team column in awayTable and homeTable
teams1 = set(qb['Team'])
teams1.remove('SF')
teams2 = set(awayTable['team'])
teams2.remove('San Francisco 49ers')
t1List = list(teams1)
t2List = list(teams2)
t1List.sort()
t2List.sort()
zipTeams = zip(t1List, t2List)
teamDict = dict(list(zipTeams))
teamDict['SF'] = 'San Francisco 49ers'
teamDict

{'ARI': 'Arizona Cardinals',
 'ATL': 'Atlanta Falcons',
 'BAL': 'Baltimore Ravens',
 'BUF': 'Buffalo Bills',
 'CAR': 'Carolina Panthers',
 'CHI': 'Chicago Bears',
 'CIN': 'Cincinnati Bengals',
 'CLE': 'Cleveland Browns',
 'DAL': 'Dallas Cowboys',
 'DEN': 'Denver Broncos',
 'DET': 'Detroit Lions',
 'GB': 'Green Bay Packers',
 'HOU': 'Houston Texans',
 'IND': 'Indianapolis Colts',
 'JAX': 'Jacksonville Jaguars',
 'KC': 'Kansas City Chiefs',
 'LAC': 'Los Angeles Chargers',
 'LAR': 'Los Angeles Rams',
 'MIA': 'Miami Dolphins',
 'MIN': 'Minnesota Vikings',
 'NE': 'New England Patriots',
 'NO': 'New Orleans Saints',
 'NYG': 'New York Giants',
 'NYJ': 'New York Jets',
 'OAK': 'Oakland Raiders',
 'PHI': 'Philadelphia Eagles',
 'PIT': 'Pittsburgh Steelers',
 'SEA': 'Seattle Seahawks',
 'TB': 'Tampa Bay Buccaneers',
 'TEN': 'Tennessee Titans',
 'WAS': 'Washington Redskins',
 'SF': 'San Francisco 49ers'}

In [43]:
teamDict2 = {'ARI': 'Cardinals',
 'ATL': 'Falcons',
 'BAL': 'Ravens',
 'BUF': 'Bills',
 'CAR': 'Panthers',
 'CHI': 'Bears',
 'CIN': 'Bengals',
 'CLE': 'Browns',
 'DAL': 'Cowboys',
 'DEN': 'Broncos',
 'DET': 'Lions',
 'GB': 'Packers',
 'HOU': 'Texans',
 'IND': 'Colts',
 'JAX': 'Jaguars',
 'KC': 'Chiefs',
 'LAC': 'Chargers',
 'LAR': 'Rams',
 'MIA': 'Dolphins',
 'MIN': 'Vikings',
 'NE': 'Patriots',
 'NO': 'Saints',
 'NYG': 'Giants',
 'NYJ': 'Jets',
 'OAK': 'Raiders',
 'PHI': 'Eagles',
 'PIT': 'Steelers',
 'SEA': 'Seahawks',
 'TB': 'Buccaneers',
 'TEN': 'Titans',
 'WAS': 'Redskins',
 'SF': '49ers'}

In [44]:
teamDict3 = zip(teamDict.values(),teamDict2.values())
teamDict3 = dict(list(teamDict3))
teamDict3

{'Arizona Cardinals': 'Cardinals',
 'Atlanta Falcons': 'Falcons',
 'Baltimore Ravens': 'Ravens',
 'Buffalo Bills': 'Bills',
 'Carolina Panthers': 'Panthers',
 'Chicago Bears': 'Bears',
 'Cincinnati Bengals': 'Bengals',
 'Cleveland Browns': 'Browns',
 'Dallas Cowboys': 'Cowboys',
 'Denver Broncos': 'Broncos',
 'Detroit Lions': 'Lions',
 'Green Bay Packers': 'Packers',
 'Houston Texans': 'Texans',
 'Indianapolis Colts': 'Colts',
 'Jacksonville Jaguars': 'Jaguars',
 'Kansas City Chiefs': 'Chiefs',
 'Los Angeles Chargers': 'Chargers',
 'Los Angeles Rams': 'Rams',
 'Miami Dolphins': 'Dolphins',
 'Minnesota Vikings': 'Vikings',
 'New England Patriots': 'Patriots',
 'New Orleans Saints': 'Saints',
 'New York Giants': 'Giants',
 'New York Jets': 'Jets',
 'Oakland Raiders': 'Raiders',
 'Philadelphia Eagles': 'Eagles',
 'Pittsburgh Steelers': 'Steelers',
 'Seattle Seahawks': 'Seahawks',
 'Tampa Bay Buccaneers': 'Buccaneers',
 'Tennessee Titans': 'Titans',
 'Washington Redskins': 'Redskins',
 'Sa

In [45]:
# Map dictionary keys to new values so we have matching team/opponent names across the board
qb['Team'] = qb['Team'].map(teamDict2)
qb['Opponent'] = qb['Opponent'].map(teamDict2)

# qbSalaries['Team'] = qbSalaries['Team'].map(teamDict2)
# qbSalaries['Opponent'] = qbSalaries['Opponent'].map(teamDict2)


awayMatchup['team_x'] = awayMatchup['team_x'].map(teamDict3)
awayMatchup['team_y'] = awayMatchup['team_y'].map(teamDict3)
homeMatchup['team_x'] = homeMatchup['team_x'].map(teamDict3)
homeMatchup['team_y'] = homeMatchup['team_y'].map(teamDict3)

awayMatchup.head()

gameId        date  season  week     team_x homeAway  \
0  201811110kan  2018-11-11    2018    10  Cardinals     away   
1  201610300car  2016-10-30    2016     8  Cardinals     away   
2  201612240sea  2016-12-24    2016    16  Cardinals     away   
3  201812300sea  2018-12-30    2018    17  Cardinals     away   
4  201712310sea  2017-12-31    2017    17  Cardinals     away   

                   stadium      roof surface      avgPf  ...  defDvoa  \
0        Arrowhead Stadium  outdoors   grass  14.857143  ...    0.065   
1  Bank of America Stadium  outdoors   grass  22.714286  ...    0.036   
2        CenturyLink Field  outdoors    turf  25.857143  ...   -0.114   
3        CenturyLink Field  outdoors    turf  13.000000  ...    0.016   
4        CenturyLink Field  outdoors    turf  18.571429  ...   -0.036   

   ptsMatchup  offMatchup  ovrMatchup  passMatchup  pblkMatchup  runMatchup  \
0   37.857143  -10.285714  -13.857143   -10.600000   -16.071429    0.657143   
1   51.285714    3.000000    4.457143    -2.228571     3.257143   -3.157143   
2   43.857143    0.757143   -3.042857     7.171429   -14.242857   -9.314286   
3   36.857143   -7.400000  -13.642857    -7.628571    -6.100000   -7.414286   
4   41.000000   -9.228571   -2.514286   -15.628571    -5.085714   -6.285714   

   offDvoaMatchup  totalDvoaMatchup  pf  
0          -0.315            -0.700  14  
1          -0.039             0.208  20  
2          -0.250            -0.160  34  
3          -0.409            -0.500  24  
4          -0.227            -0.159  26  

[5 rows x 41 columns]

In [46]:
#turn seasons to numeric instead of strings
qb['season'] = pd.to_numeric(qb['season'])
# qbSalaries['season'] = pd.to_numeric(qbSalaries['season'])

# Merge qb table with matchup tables, then put the two together
qbTable1 = pd.merge(qb,awayMatchup,how='inner',left_on=['Team','season','Week'],right_on=['team_x','season','week'])

qbTable2 = pd.merge(qb,homeMatchup,how='inner',left_on=['Team','season','Week'],right_on=['team_x','season','week'])

qbTableFinal = pd.concat([qbTable1,qbTable2],axis=0)

qbTableFinal.head()

# rbTableFinal = pd.merge(rbTable,rbSalaries,how='inner',left_on=['Name', 'Team', 'Position', 'Week', 'Opponent','season'],right_on=['Name', 'Team', 'Position', 'Week', 'Opponent','season'])
# rbTableFinal.columns

Rank              Name      Team Position  Week    Opponent  \
0     2  Matthew Stafford     Lions       QB    17     Packers   
1     4        Cam Newton  Panthers       QB    13  Buccaneers   
2    10        Cam Newton  Panthers       QB     4       Bears   
3    13     Aaron Rodgers   Packers       QB    13      Giants   
4    18     Aaron Rodgers   Packers       QB     9    Chargers   

   PassingCompletions  PassingAttempts  PassingCompletionPercentage  \
0                  36               59                         61.0   
1                  12               21                         57.1   
2                  27               46                         58.7   
3                  28               46                         60.9   
4                  21               26                         80.8   

   PassingYards  ...  defDvoa  ptsMatchup  offMatchup  ovrMatchup  \
0           520  ...    0.111   47.571429    5.271429   -4.171429   
1           204  ...    0.163   53.857143   14.500000    4.842857   
2           374  ...    0.059   37.142857    7.357143    5.314286   
3           369  ...   -0.010   60.571429   13.242857    3.985714   
4           247  ...    0.126   55.571429   15.714286    5.842857   

   passMatchup  pblkMatchup  runMatchup  offDvoaMatchup  totalDvoaMatchup  pf  
0    -4.814286    17.314286    8.114286           0.195            -0.178  41  
1     8.257143     3.157143   15.257143           0.313            -0.103  38  
2     2.342857     8.242857    0.371429           0.186            -0.066  29  
3    21.114286    14.871429    3.685714           0.369             0.095  38  
4    22.000000     7.214286    0.885714           0.499             0.399  45  

[5 rows x 61 columns]

In [47]:
qbs = qbTableFinal[(qbTableFinal['PassingAttempts'] >= 10)]

qbs = pd.merge(qbs,oddsTable,how='inner',left_on=['Team','season','Week'],right_on=['team','season','week'])

qbs.loc[qbs.pf > qbs.pa, 'winLose'] = 'Win'
qbs.loc[qbs.pf < qbs.pa, 'winLose'] = 'Loss'
qbs.loc[qbs.pf == qbs.pa, 'winLose'] = 'Tie'

qbs.loc[qbs.totalScore > qbs.total, 'result'] = 'over'
qbs.loc[qbs.totalScore < qbs.total, 'result'] = 'under'
qbs.loc[qbs.totalScore == qbs.total, 'result'] = 'push'

# Turn date column into datetime data
qbs['date_x'] = pd.to_datetime(qbs['date_x'])

# Create a PT/A column
qbs['PassingTouchdownsPerAttempt'] = qbs['PassingTouchdowns'] / qbs['PassingAttempts']

In [48]:
# Create a column of running averages for each player's fantasy points. Use previous 7-game averages

qbs = qbs.set_index(['date_x','Name'])
qbs.sort_index().groupby('Name').get_group('Matthew Stafford')['FantasyPointsFanDuel']



date_x      Name            
2011-09-18  Matthew Stafford    26.86
2011-09-25  Matthew Stafford    23.02
2011-10-02  Matthew Stafford    16.50
2011-10-10  Matthew Stafford    15.86
2011-10-16  Matthew Stafford    20.62
                                ...  
2018-12-02  Matthew Stafford    11.00
2018-12-09  Matthew Stafford     4.74
2018-12-16  Matthew Stafford    12.32
2018-12-23  Matthew Stafford     4.64
2018-12-30  Matthew Stafford    18.44
Name: FantasyPointsFanDuel, Length: 118, dtype: float64

In [49]:
qbs['FantasyPointsPerGame7'] = qbs.sort_index().groupby('Name')['FantasyPointsFanDuel'].apply(lambda x: x.shift(1).rolling(window=7).mean())
qbs['avgPassingRating7'] = qbs.sort_index().groupby('Name')['PassingRating'].apply(lambda x: x.shift(1).rolling(window=7).mean())
qbs['avgPassingTouchdowns7'] = qbs.sort_index().groupby('Name')['PassingTouchdowns'].apply(lambda x: x.shift(1).rolling(window=7).mean())
qbs['avgPYA'] = qbs.sort_index().groupby('Name')['PassingYardsPerAttempt'].apply(lambda x: x.shift(1).rolling(window=7).mean())


qbs = qbs.fillna(method='bfill')
qbs = qbs.reset_index()

In [50]:
tester = qbs[['Name','date_x','season','Week','PassingYardsPerAttempt','avgPYA']].sort_values(['Name','date_x'])
tester[tester['Name'] == 'Kirk Cousins']

Name     date_x  season  Week  PassingYardsPerAttempt    avgPYA
271   Kirk Cousins 2012-12-16    2012    15                     8.9  8.057143
2575  Kirk Cousins 2013-12-08    2013    14                     3.7  7.757143
507   Kirk Cousins 2013-12-15    2013    15                     8.5  7.842857
2586  Kirk Cousins 2013-12-22    2013    16                     5.5  6.442857
714   Kirk Cousins 2013-12-29    2013    17                     3.4  6.814286
...            ...        ...     ...   ...                     ...       ...
1866  Kirk Cousins 2018-12-02    2018    13                     4.6  7.771429
1857  Kirk Cousins 2018-12-10    2018    14                     6.3  7.228571
3750  Kirk Cousins 2018-12-16    2018    15                    10.2  6.971429
1745  Kirk Cousins 2018-12-23    2018    16                     9.0  7.442857
3804  Kirk Cousins 2018-12-30    2018    17                     4.0  7.471429

[69 rows x 6 columns]

In [51]:
qbs.columns

Index(['date_x', 'Name', 'Rank', 'Team', 'Position', 'Week', 'Opponent',
       'PassingCompletions', 'PassingAttempts', 'PassingCompletionPercentage',
       'PassingYards', 'PassingYardsPerAttempt', 'PassingTouchdowns',
       'PassingInterceptions', 'PassingRating', 'RushingAttempts',
       'RushingYards', 'RushingYardsPerAttempt', 'RushingTouchdowns',
       'FantasyPointsPerGameFanDuel', 'FantasyPointsFanDuel', 'season',
       'gameId', 'week_x', 'team_x', 'homeAway', 'stadium', 'roof', 'surface',
       'avgPf', 'avgOvr_x', 'avgOff', 'avgPass', 'avgPblk', 'avgRecv',
       'avgRun', 'avgRblk', 'totalDvoa_x', 'offDvoa', 'stDvoa', 'overUnder',
       'pa', 'totalScore', 'team_y', 'avgPa', 'avgOvr_y', 'avgDef', 'avgRdef',
       'avgPrsh', 'avgCov', 'totalDvoa_y', 'defDvoa', 'ptsMatchup',
       'offMatchup', 'ovrMatchup', 'passMatchup', 'pblkMatchup', 'runMatchup',
       'offDvoaMatchup', 'totalDvoaMatchup', 'pf', 'date_y', 'week_y', 'team',
       'spread', 'total', 'moneyLine'

In [52]:
qbVars = ['gameId','Name', 'Team', 'season', 'Week', 'Opponent', 'homeAway','surface','roof', 'PassingCompletions','PassingAttempts',
          'PassingCompletionPercentage','PassingYards','PassingYardsPerAttempt','avgPYA','PassingTouchdowns','avgPassingTouchdowns7','PassingTouchdownsPerAttempt',
          'PassingInterceptions','PassingRating','avgPassingRating7','RushingAttempts','RushingYards', 'RushingYardsPerAttempt',
          'RushingTouchdowns','avgPf', 'avgOvr_x', 'avgOff', 'avgPass', 'avgPblk', 'avgRecv',
          'avgRun', 'avgRblk', 'totalDvoa_x', 'offDvoa', 'stDvoa','pa','avgPa','avgOvr_y', 'avgDef', 'avgRdef',
          'avgPrsh', 'avgCov', 'totalDvoa_y', 'defDvoa', 'ptsMatchup',
          'offMatchup', 'ovrMatchup', 'passMatchup', 'pblkMatchup', 'runMatchup',
          'offDvoaMatchup', 'totalDvoaMatchup', 'pf','spread','total','impliedTotal','result','winLose',
          'FantasyPointsPerGame7','FantasyPointsFanDuel']
catQbVars = ['homeAway', 'surface', 'roof','winLose', 'result']

In [53]:
newQbs = qbs[qbVars]
newQbs.tail()

gameId              Name     Team  season  Week  Opponent  \
3842  201810140rai        Derek Carr  Raiders    2018     6  Seahawks   
3843  201812230det  Matthew Stafford    Lions    2018    16   Vikings   
3844  201812230det       Matt Cassel    Lions    2018    16   Vikings   
3845  201811180jax     Blake Bortles  Jaguars    2018    11  Steelers   
3846  201811110nyj       Josh McCown     Jets    2018    10     Bills   

     homeAway surface      roof  PassingCompletions  ...  offDvoaMatchup  \
3842     home   grass  outdoors                  23  ...          -0.037   
3843     home    turf      dome                  18  ...          -0.144   
3844     home    turf      dome                   5  ...          -0.144   
3845     home   grass  outdoors                  10  ...          -0.140   
3846     home    turf  outdoors                  17  ...          -0.349   

      totalDvoaMatchup  pf  spread  total  impliedTotal  result  winLose  \
3842            -0.029   3     3.0   47.5         22.25   under     Loss   
3843            -0.232   9     6.5   42.5         18.00   under     Loss   
3844            -0.232   9     6.5   42.5         18.00   under     Loss   
3845            -0.133  16     4.0   47.0         21.50   under     Loss   
3846             0.298  10    -7.0   37.5         22.25    over     Loss   

      FantasyPointsPerGame7  FantasyPointsFanDuel  
3842              16.454286                  4.78  
3843              10.474286                  4.64  
3844               6.434286                  3.20  
3845              18.080000                  3.86  
3846              18.554286                  3.80  

[5 rows x 61 columns]

In [54]:
corr = newQbs.corr()
corr.style.background_gradient(cmap='coolwarm')

In [55]:
rollAvgGameData.head()

date      team        gameId  totExp   oTot  oPass  oRush  oTov  \
0  2010-09-09   Vikings  201009090nor    -5.0  -6.45  -5.54  -0.91 -4.17   
1  2010-09-09    Saints  201009090nor     5.0   2.86   4.60  -1.42  0.00   
2  2010-09-12   Falcons  201009120pit    -6.0  -8.90  -4.99  -3.91 -3.92   
3  2010-09-12  Steelers  201009120pit     6.0  -3.01  -0.92  -1.43 -3.79   
4  2010-09-12    Titans  201009120oti    25.0  10.04   6.91   3.79 -4.66   

    dTot  dPass  ...  passCompAvg  passAttAvg  passYdsAvg  passTdsAvg  \
0  -2.86  -4.60  ...    21.142857   36.714286  224.285714    1.285714   
1   6.45   5.54  ...    21.142857   36.714286  224.285714    1.285714   
2   3.01   0.92  ...    21.142857   36.714286  224.285714    1.285714   
3   8.90   4.99  ...    21.142857   36.714286  224.285714    1.285714   
4  14.46  12.28  ...    21.142857   36.714286  224.285714    1.285714   

    intsAvg  timesSackedAvg  yardsLostOnSacksAvg  totalSecondsAvg  \
0  1.142857        2.571429            15.428571      1748.857143   
1  1.142857        2.571429            15.428571      1748.857143   
2  1.142857        2.571429            15.428571      1748.857143   
3  1.142857        2.571429            15.428571      1748.857143   
4  1.142857        2.571429            15.428571      1748.857143   

   lateDownConvAvg  lateDownAttAvg  
0         5.571429       15.285714  
1         5.571429       15.285714  
2         5.571429       15.285714  
3         5.571429       15.285714  
4         5.571429       15.285714  

[5 rows x 69 columns]

In [56]:
rollAvgGameData.columns

Index(['date', 'team', 'gameId', 'totExp', 'oTot', 'oPass', 'oRush', 'oTov',
       'dTot', 'dPass', 'dRush', 'dTov', 'stTot', 'stKo', 'stKr', 'stP',
       'stPr', 'fgxp', 'firstDowns', 'netPyds', 'totYds', 'to', 'rushAtt',
       'rushYds', 'rushTds', 'passComp', 'passAtt', 'passYds', 'passTds',
       'ints', 'timesSacked', 'yardsLostOnSacks', 'fumbles', 'fumblesLost',
       'totalSeconds', 'lateDownConv', 'lateDownAtt', 'totExpAvg', 'oTotAvg',
       'oPassAvg', 'oRushAvg', 'oTovAvg', 'dTotAvg', 'dPassAvg', 'dRushAvg',
       'dTovAvg', 'stTotAvg', 'stKoAvg', 'stKrAvg', 'stPAvg', 'stPrAvg',
       'fgxpAvg', 'firstDownsAvg', 'netPydsAvg', 'totYdsAvg', 'toAvg',
       'rushAttAvg', 'rushYdsAvg', 'rushTdsAvg', 'passCompAvg', 'passAttAvg',
       'passYdsAvg', 'passTdsAvg', 'intsAvg', 'timesSackedAvg',
       'yardsLostOnSacksAvg', 'totalSecondsAvg', 'lateDownConvAvg',
       'lateDownAttAvg'],
      dtype='object')

In [57]:
# Setup a list for offensive columns and defensive columns from the rollAvgGameData table
# goal is to join a player's offensive metrics from roll avg table, and his opponent's defensive metrics

offRollCols = ['date','gameId','team','oTot', 'oPass', 'oRush', 'oTov','firstDowns', 'netPyds', 'totYds','passTds', 'to',
       'timesSacked', 'yardsLostOnSacks', 'fumbles', 'fumblesLost',
       'totalSeconds', 'lateDownConv', 'lateDownAtt', 'totExpAvg', 'oTotAvg',
       'oPassAvg', 'oRushAvg', 'oTovAvg','firstDownsAvg', 'netPydsAvg', 'totYdsAvg', 'toAvg',
       'passCompAvg', 'passAttAvg', 'passYdsAvg', 'passTdsAvg', 'intsAvg', 'timesSackedAvg',
       'yardsLostOnSacksAvg', 'totalSecondsAvg', 'lateDownConvAvg',
       'lateDownAttAvg']

defRollCols = ['date','gameId','team','dTot', 'dPass', 'dRush', 'dTov','dTotAvg', 'dPassAvg', 'dRushAvg', 'dTovAvg']

offRollTable = rollAvgGameData[offRollCols]

defRollTable = rollAvgGameData[defRollCols]
defRollTable.head()

date        gameId      team   dTot  dPass  dRush   dTov   dTotAvg  \
0  2010-09-09  201009090nor   Vikings  -2.86  -4.60   1.42   0.00  4.021429   
1  2010-09-09  201009090nor    Saints   6.45   5.54   0.91   4.17  4.021429   
2  2010-09-12  201009120pit   Falcons   3.01   0.92   1.43   3.79  4.021429   
3  2010-09-12  201009120pit  Steelers   8.90   4.99   3.91   3.92  4.021429   
4  2010-09-12  201009120oti    Titans  14.46  12.28  -1.81  11.46  4.021429   

   dPassAvg  dRushAvg   dTovAvg  
0  0.408571  2.307143  6.574286  
1  0.408571  2.307143  6.574286  
2  0.408571  2.307143  6.574286  
3  0.408571  2.307143  6.574286  
4  0.408571  2.307143  6.574286

In [58]:
newQbs = newQbs.merge(offRollTable,left_on=['gameId','Team'],right_on=['gameId','team'])
newQbs['passTds']

0       5
1       1
2       1
3       4
4       4
       ..
3749    3
3750    3
3751    3
3752    2
3753    0
Name: passTds, Length: 3754, dtype: int64

In [59]:
newQbs.head()

gameId              Name      Team  season  Week    Opponent  \
0  201201010gnb  Matthew Stafford     Lions    2011    17     Packers   
1  201112040tam        Cam Newton  Panthers    2011    13  Buccaneers   
2  201110020chi        Cam Newton  Panthers    2011     4       Bears   
3  201112040nyg     Aaron Rodgers   Packers    2011    13      Giants   
4  201111060sdg     Aaron Rodgers   Packers    2011     9    Chargers   

  homeAway surface      roof  PassingCompletions  ...  passCompAvg  \
0     away   grass  outdoors                  36  ...    24.285714   
1     away   grass  outdoors                  12  ...    20.428571   
2     away   grass  outdoors                  27  ...    17.571429   
3     away    turf  outdoors                  28  ...    24.000000   
4     away   grass  outdoors                  21  ...    25.857143   

   passAttAvg  passYdsAvg  passTdsAvg   intsAvg  timesSackedAvg  \
0   40.285714  294.571429    2.285714  1.142857        2.142857   
1   32.000000  249.142857    1.000000  1.000000        2.142857   
2   29.571429  214.285714    1.000000  0.714286        2.857143   
3   35.714286  269.285714    1.571429  1.285714        2.571429   
4   39.714286  341.571429    2.000000  1.428571        2.857143   

   yardsLostOnSacksAvg  totalSecondsAvg  lateDownConvAvg  lateDownAttAvg  
0            17.714286      1811.857143         6.000000       14.428571  
1            13.285714      1865.000000         6.142857       13.000000  
2            17.714286      1705.571429         4.000000       14.142857  
3            16.428571      1784.571429         4.571429       12.142857  
4            21.142857      1755.428571         5.428571       13.142857  

[5 rows x 98 columns]

In [60]:
# Create a column of running averages for each player's fantasy points. Use previous 7-game averages

qb2 = newQbs.set_index(['date','Opponent'])
qb2.sort_index().groupby('Opponent').get_group('Packers')['PassingYards']

date        Opponent
2011-09-18  Packers     432
2011-09-25  Packers     302
2011-10-02  Packers     273
2011-10-09  Packers     167
2011-10-16  Packers     321
                       ... 
2018-12-02  Packers     149
2018-12-09  Packers     262
2018-12-16  Packers     235
2018-12-23  Packers     341
2018-12-30  Packers     266
Name: PassingYards, Length: 115, dtype: int64

In [61]:
qb2 = qb2[~qb2.index.duplicated()]

In [62]:
qb2['defPassingYardsAllowed7'] = qb2.sort_index().groupby('Opponent')['PassingYards'].apply(lambda x: x.shift(1).rolling(window=7).mean())
qb2['defOtotAllowed7'] = qb2.sort_index().groupby('Opponent')['oTot'].apply(lambda x: x.shift(1).rolling(window=7).mean())
qb2['defOpassAllowed7'] = qb2.sort_index().groupby('Opponent')['oPass'].apply(lambda x: x.shift(1).rolling(window=7).mean())
qb2['defFirstDownsAllowed7'] = qb2.sort_index().groupby('Opponent')['firstDowns'].apply(lambda x: x.shift(1).rolling(window=7).mean())
qb2['defPassTdsAllowed7'] = qb2.sort_index().groupby('Opponent')['passTds'].apply(lambda x: x.shift(1).rolling(window=7).mean())
qb2['defPassingRatingAllowed7'] = qb2.sort_index().groupby('Opponent')['PassingRating'].apply(lambda x: x.shift(1).rolling(window=7).mean())
qb2['defFantasyPointsAllowed7'] = qb2.sort_index().groupby('Opponent')['FantasyPointsFanDuel'].apply(lambda x: x.shift(1).rolling(window=7).mean())
qb2['defPYAallowed7'] = qb2.sort_index().groupby('Opponent')['PassingYardsPerAttempt'].apply(lambda x: x.shift(1).rolling(window=7).mean())



qb2 = qb2.fillna(method='bfill')
qb2 = qb2.reset_index()

In [63]:
tester = qb2[['Name','date','Opponent','season','Week','PassingYardsPerAttempt','defPYAallowed7','FantasyPointsFanDuel']].sort_values(['Opponent','date'])
tester[tester['Opponent'] == 'Browns']

Name        date Opponent  season  Week  \
2015       Kerry Collins  2011-09-18   Browns    2011     2   
108           Chad Henne  2011-09-25   Browns    2011     3   
50       Matt Hasselbeck  2011-10-02   Browns    2011     4   
2027         Kyle Boller  2011-10-16   Browns    2011     6   
215   Charlie Whitehurst  2011-10-23   Browns    2011     7   
...                  ...         ...      ...     ...   ...   
3558      Deshaun Watson  2018-12-02   Browns    2018    13   
1753          Cam Newton  2018-12-09   Browns    2018    14   
3584         Case Keenum  2018-12-15   Browns    2018    15   
1695        Jeff Driskel  2018-12-23   Browns    2018    16   
3460       Lamar Jackson  2018-12-30   Browns    2018    17   

      PassingYardsPerAttempt  defPYAallowed7  FantasyPointsFanDuel  
2015                     5.0        9.428571                  8.54  
108                      8.8        5.500000                 14.70  
50                      11.0        6.028571                 20.30  
2027                     7.1        8.285714                  4.90  
215                      3.2        6.742857                  1.18  
...                      ...             ...                   ...  
3558                     7.2        7.585714                 15.96  
1753                     6.3        7.857143                 11.90  
3584                     5.4        7.271429                 14.38  
1695                     7.0        7.042857                 17.42  
3460                     7.5        7.028571                 26.16  

[113 rows x 8 columns]

In [64]:
qb2['yardsMatchup'] = qb2['defPassingYardsAllowed7'] + qb2['passYdsAvg']
qb2['oTotMatchup'] = qb2['oTotAvg'] + qb2['defOtotAllowed7']
qb2['oPassMatchup'] = qb2['oPassAvg'] + qb2['defOpassAllowed7']
qb2['firstDownMatchup'] = qb2['firstDownsAvg'] + qb2['defFirstDownsAllowed7']
qb2['passTdMatchup'] = qb2['avgPassingTouchdowns7'] + qb2['defPassTdsAllowed7']
qb2['passingRatingMatchup'] = qb2['avgPassingRating7'] + qb2['defPassingRatingAllowed7']
qb2['fptsMatchup'] = qb2['FantasyPointsPerGame7'] + qb2['defFantasyPointsAllowed7']
qb2['PYAMatchup'] = qb2['avgPYA'] + qb2['defPYAallowed7']

In [65]:
corr = qb2.corr()
corr.style.background_gradient(cmap='coolwarm')

In [66]:
qb2.to_csv('C://Users//Michael//Desktop//Springboard//Capstone2//csvFiles//qbModelData.csv')

In [74]:
lookVars = ['Name','date','Opponent','season','Week','homeAway','PassingTouchdowns','RushingTouchdowns','defDvoa','spread','total','pf','pa','impliedTotal','result','FantasyPointsFanDuel']

In [77]:
tb = qb2[qb2['Name'] == 'Aaron Rodgers']
# tb.corr().style.background_gradient(cmap='coolwarm')
tb[(tb['impliedTotal'] >= 24) & (tb['homeAway'] == 'home') & ((tb['pf'] - tb['pa']) <= -1*tb['spread'])][lookVars].sort_values('FantasyPointsFanDuel',ascending=False)

Name        date    Opponent  season  Week homeAway  \
2056  Aaron Rodgers  2012-09-30      Saints    2012     4     home   
2490  Aaron Rodgers  2014-09-14        Jets    2014     2     home   
3445  Aaron Rodgers  2018-10-15       49ers    2018     6     home   
2495  Aaron Rodgers  2014-12-08     Falcons    2014    14     home   
2957  Aaron Rodgers  2016-11-06       Colts    2016     9     home   
3210  Aaron Rodgers  2017-09-24     Bengals    2017     3     home   
1845  Aaron Rodgers  2011-11-20  Buccaneers    2011    11     home   
2779  Aaron Rodgers  2015-11-15       Lions    2015    10     home   
2807  Aaron Rodgers  2015-10-18    Chargers    2015     6     home   
3045  Aaron Rodgers  2016-10-09      Giants    2016     5     home   
3571  Aaron Rodgers  2018-12-02   Cardinals    2018    13     home   
2869  Aaron Rodgers  2015-11-26       Bears    2015    12     home   
3104  Aaron Rodgers  2016-10-16     Cowboys    2016     6     home   

      PassingTouchdowns  RushingTouchdowns  defDvoa  spread  total  pf  pa  \
2056                  4                  0    0.342    -7.5   54.0  28  27   
2490                  3                  0   -0.029    -7.0   46.5  31  24   
3445                  2                  0    0.047    -9.0   46.5  33  30   
2495                  3                  0    0.165   -14.0   54.0  43  37   
2957                  3                  0    0.223    -7.5   52.0  26  31   
3210                  3                  0   -0.061    -7.0   47.5  27  24   
1845                  3                  0    0.140   -13.5   48.5  35  26   
2779                  2                  0    0.148   -10.0   50.0  16  18   
2807                  2                  0    0.080   -10.0   50.0  27  20   
3045                  2                  0    0.007    -7.0   48.5  23  16   
3571                  1                  0   -0.069   -13.0   41.0  17  20   
2869                  1                  0    0.082    -8.0   45.0  13  17   
3104                  1                  0    0.073    -5.5   47.5  16  30   

      impliedTotal result  FantasyPointsFanDuel  
2056         30.75   over                 29.06  
2490         26.75   over                 28.64  
3445         27.75   over                 28.40  
2495         34.00   over                 27.88  
2957         29.75   over                 27.18  
3210         27.25   over                 25.82  
1845         31.00   over                 25.76  
2779         30.00  under                 22.12  
2807         30.00  under                 19.60  
3045         27.75  under                 17.86  
3571         27.00  under                 15.32  
2869         26.50  under                 14.38  
3104         26.50  under                 13.46

In [36]:
ben = tb[(tb['impliedTotal'] >= 18)]
np.mean(ben['FantasyPointsFanDuel'])

24.157894736842106

In [88]:
totalInstances = len(ben)
hits = len(ben[ben['FantasyPointsFanDuel'] > 20])
rate = hits/totalInstances

print(hits,totalInstances,rate)

ben[lookVars].sort_values('FantasyPointsFanDuel',ascending=False)

39 103 0.3786407766990291


Name        date  Opponent  season  Week homeAway  \
2478  Ben Roethlisberger  2014-10-26     Colts    2014     8     home   
3422  Ben Roethlisberger  2018-09-16    Chiefs    2018     2     home   
3424  Ben Roethlisberger  2018-11-08  Panthers    2018    10     home   
2481  Ben Roethlisberger  2014-11-02    Ravens    2014     9     home   
2940  Ben Roethlisberger  2016-10-02    Chiefs    2016     4     home   
...                  ...         ...       ...     ...   ...      ...   
867   Ben Roethlisberger  2014-09-11    Ravens    2014     2     away   
3391  Ben Roethlisberger  2017-10-08   Jaguars    2017     5     home   
1099  Ben Roethlisberger  2015-09-27      Rams    2015     3     away   
1102  Ben Roethlisberger  2015-12-27    Ravens    2015    16     away   
1341  Ben Roethlisberger  2016-12-11     Bills    2016    14     away   

      PassingTouchdowns  RushingTouchdowns  defDvoa  spread  total  \
2478                  6                  0    0.039     4.5   48.0   
3422                  3                  1    0.038    -4.5   52.0   
3424                  5                  0   -0.002    -3.5   51.0   
2481                  6                  0   -0.088    -2.5   48.0   
2940                  5                  0   -0.056    -3.5   48.5   
...                 ...                ...      ...     ...    ...   
867                   0                  0   -0.019     2.5   44.5   
3391                  0                  0   -0.187    -7.0   41.0   
1099                  0                  0   -0.153     1.0   48.0   
1102                  0                  0    0.066   -11.0   47.5   
1341                  0                  0    0.033    -2.0   46.0   

      impliedTotal result  FantasyPointsFanDuel  
2478         21.75   over                 44.78  
3422         28.25   over                 38.98  
3424         27.25   over                 35.82  
2481         25.25   over                 35.70  
2940         26.00   over                 33.90  
...            ...    ...                   ...  
867          21.00  under                  7.68  
3391         24.00  under                  7.58  
1099         23.50  under                  6.68  
1102         29.25  under                  6.50  
1341         24.00   over                  5.60  

[103 rows x 14 columns]